# Space-time partial differential equation: Study of the diffusive equation (implicit methods)

Let's consider now the viscous term in Burger's equation: 

$$\frac{\partial u}{\partial t} = \nu \frac{\partial^2 u}{\partial x^2}, \tag{1}$$

## 1- Apply an explicit method. 

What would be the CFL condition for a viscous term where $\nu$ is either a constant or an array that depends on $x$. We would like to solve equation (1) numerically for $x  [x_0, x_f]$ with $x_0 = −2.6$, $x_f = 2.6$, periodic boundary conditions and with the initial condition:

$$u(x,t=t_0) = A\exp(-(x-x_0)^2/W^2)   \tag{2}$$

with $A=0.3$, $W=0.1$, and $x_0=0$. __Suggestion__: Apply the first derivative upwind and the second downwind. Apply Von Newman analysis. Is it stable? What is the time-step dependence with $\Delta x$? 

How many steps are needed to reach a $t=1.8$ for $nump=128$? And $256$? 

In [1]:
import numpy as np 
import matplotlib.pyplot as plt 
from nm_lib import nm_lib as nm
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

In [2]:
def initial_u(xx): 
    W = 0.1
    A = 0.3
    x0 = 0

    return A*np.exp(-(xx-x0)**2/W**2)

Add the steps for writing the viscosity term as a discretized equation, and then show how we end up with: 

$$
\frac{\nu \Delta t}{dx^2} \leq \frac{1}{2}
$$

As long as the condition is fulfilled, it is stable ??

In [3]:
""" 
Here I have now just assumed that nu is a constant or something. I actually just forgot it when doing this :)
"""

nint = 128
nump = nint+1 

nint2 = 256
nump2 = nint2+1

x0 = -2.6
xf = 2.6

x = np.linspace(x0,xf,nump)
x2 = np.linspace(x0,xf,nump2)


dx = x[1]-x[0]
dx2 = x2[1] - x2[0]

t = 0
t2 = 0
steps = 0
steps2 = 0

dt = dx**2/2
dt2 = dx2**2/2

print("dt with nint = 128: ", dt)
print("dt with nint = 256: ", dt2, "\n")

while t <= 1.8: 
    t += dt 
    steps += 1
    

while t2 <= 1.8: 
    t2 += dt2
    steps2 += 1

print("Number of steps needed for nint = 128: ", steps)
print("Number of steps needed for nint = 256: ", steps2, "\n")


dt with nint = 128:  0.0008251953124999964
dt with nint = 256:  0.0002062988281250036 

Number of steps needed for nint = 128:  2182
Number of steps needed for nint = 256:  8726 



In [4]:
def deriv2(xx,hh): 

    dx = xx[1] - xx[0]
    u_deriv = (np.roll(hh,-1) - 2*hh + np.roll(hh,1))/dx**2

    return u_deriv

In [5]:
def cfl_ddx2(nu,xx):

    dx = xx[1] - xx[0]
    return np.min(dx**2/(2*np.abs(nu)))

In [6]:
def step(xx, hh, a, cfl_cut = 0.98, 
                    ddx = lambda x,y: nm.deriv_dnw(x, y, roll=True), **kwargs): 
    
    dt = cfl_cut*cfl_ddx2(a,xx)
    rhs = a*ddx(xx,hh)
    return dt, rhs

In [7]:
def evolve(xx, hh, nt, a, cfl_cut = 0.48, 
        ddx = lambda x,y: nm.deriv_dnw(x, y), 
        bnd_type='wrap', bnd_limits=[0,1], **kwargs):

    t = np.zeros(nt)
    un = np.zeros((len(xx), nt))

    un[:,0] = hh
    d = len(un)

    for i in range(nt-1):


        dt, rhs = step(xx, hh, a, cfl_cut = cfl_cut ,ddx = ddx) 
        un[:,i+1] = hh + rhs*dt
        t[i+1] = t[i]+dt
        un[:,i+1] = np.pad(un[bnd_limits[0]:d- bnd_limits[1],i+1], bnd_limits, bnd_type)
        hh = un[:,i+1]
        
    return t, un

In [8]:
nt = 100
nu = 1

u0 = initial_u(x)

t, un = evolve(x, u0, nt , nu  ,ddx = deriv2, bnd_limits=[1,0])

In [9]:
plt.ioff()

fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    axes.plot(x,un[:,0])

def animate(i):
 
    axes.clear()
    axes.plot(x,un[:,i])
    axes.set_title('t=%.2f'%t[i])
    axes.grid()
    
anim = FuncAnimation(fig, animate, interval=50, frames=nt, init_func=init)
HTML(anim.to_jshtml())

In [10]:
plt.close()

## Choose one of the following options: 

## 2- Implicit methods.

In the [wiki](https://github.com/AST-Course/AST5110/wiki/Implicit-methods), we describe some implicit or semi-explicit methods that allow relaxing the CFL constraint on diffusive terms. Consider Newton-Rapson method and repeat the previous numerical experiment. For this, you will need to implement the following   


$F_j = u^{n+1}_j - u^n_j - \nu \, (u^{n+1}_{j+1} - 2u^{n+1}_{j}+u^{n+1}_{j-1})\frac{\Delta t}{\Delta x^2}$

in `NR_f` and `step_diff_burgers` functions in `nm_lib`. 

And the Jacobian can be easily built. 

$J(j,k) = F_j'(u^{n+1}_k)$

fill in the `jacobian` function in `nm_lib`. Note that this matrix is linear with $u$. 

Test the model with [wiki](https://github.com/AST-Course/AST5110/wiki/Self-similar-solution-for-parabolic-eq) self-similar solutions. How long it takes each time step compared to the Lax-method? Use `time.time` library. Do it for nump=256, nt=30 and dt = 0.1. In order to test the simulation, use `curve_fit` from `scipy.optimize`. 

__hint__ consider to use a good initial guess (`p0`) in and `bnd_limits` to facilitate the fitting wiht `curve_fit`. What happens to the solution when increasing dt? How much can be improved in limiting the tolerance?

----------------------------------------------

Let's consider a non-linear function where $\nu$ depends on $u$. To keep it simple, solve the following: 

$\frac{\partial u}{\partial t} = u \frac{\partial^2 u}{\partial x^2}$

where $\nu_0$ is a constant and the same initial conditions as the previous exercise (fill in `Newton_Raphson_u`, `jacobian_u` and `NR_f_u`. Consider an error limit of $10^{-4}$ and compare the previous exercise (with the same error limit). How many iterations needs now the method to converge to the right solution? Why? Increase `ncount` to 1000. 

## 3- Semi-explicit methods. 

__a)__ Super-time-stepping (STS) schemes work for parabolic terms. STS is an API method that performs a subset of "unstable" intermediate steps, but the sum of all the steps is stable. Visualize how `taui_sts` varies with $nu$ and $niter$. Compare the solution with the analytical one for the final and intermediate STS steps. For the full STS steps, how improves the solution with $nu$? and $niter$? Is there a relation between the error and these two parameters, $nu$, and $niter$? For which $niter$ and $nu$ the method provides larger steps than an ordinary explicit. For this exercise, fill in `evol_sts`, and `taui_sts`. 

In [11]:
nt = 100

t, un = nm.evol_sts(x, u0, nt , nu , ddx = deriv2, bnd_limits=[0,1], nu=0.9, n_sts=4)

In [12]:
plt.ioff()

fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    axes.plot(x,un[:,0])

def animate(i):
 
    axes.clear()
    axes.plot(x,un[:,i])
    axes.set_title('t=%.2f'%t[i])
    axes.grid()
    
anim = FuncAnimation(fig, animate, interval=50, frames=nt, init_func=init)
HTML(anim.to_jshtml())